In [1]:

import types
import pandas as pd
from botocore.client import Config
import ibm_boto3

def __iter__(self): return 0

# @hidden_cell
# The following code accesses a file in your IBM Cloud Object Storage. It includes your credentials.
# You might want to remove those credentials before you share the notebook.
client_9bb55b339344496a999e584aaead2498 = ibm_boto3.client(service_name='s3',
    ibm_api_key_id='f0EACs29OmW53d9ds_JjT6DvHO3clTQulRccKYKHZ6-B',
    ibm_auth_endpoint="https://iam.cloud.ibm.com/oidc/token",
    config=Config(signature_version='oauth'),
    endpoint_url='https://s3-api.us-geo.objectstorage.service.networklayer.com')

body = client_9bb55b339344496a999e584aaead2498.get_object(Bucket='cbse-donotdelete-pr-6ddd8vqrcdeho5',Key='Data-Collisions.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

df_accd = pd.read_csv(body)
df_accd.head()


/opt/conda/envs/Python36/lib/python3.6/site-packages/IPython/core/interactiveshell.py:3020: DtypeWarning: Columns (33) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


SEVERITYCODE           X          Y  OBJECTID  INCKEY  COLDETKEY  \
0           Injury -122.323148  47.703140         1    1307       1307   
1  Property Damage -122.347294  47.647172         2   52200      52200   
2  Property Damage -122.334540  47.607871         3   26700      26700   
3  Property Damage -122.334803  47.604803         4    1144       1144   
4           Injury -122.306426  47.545739         5   17700      17700   

  REPORTNO   STATUS      ADDRTYPE   INTKEY  ... ROADCOND  \
0  3502005  Matched  Intersection  37475.0  ...      Wet   
1  2607959  Matched         Block      NaN  ...      Wet   
2  1482393  Matched         Block      NaN  ...      Dry   
3  3503937  Matched         Block      NaN  ...      Dry   
4  1807429  Matched  Intersection  34387.0  ...      Wet   

                 LIGHTCOND PEDROWNOTGRNT  SDOTCOLNUM SPEEDING ST_COLCODE  \
0                 Daylight           NaN         NaN      NaN         10   
1  Dark - Street Lights On           NaN   6354039.0      NaN         11   
2                 Daylight           NaN   4323031.0      NaN         32   
3                 Daylight           NaN         NaN      NaN         23   
4                 Daylight           NaN   4028032.0      NaN         10   

                                          ST_COLDESC  SEGLANEKEY  \
0                                  Entering at angle           0   
1  From same direction - both going straight - bo...           0   
2                             One parked--one moving           0   
3                   From same direction - all others           0   
4                                  Entering at angle           0   

   CROSSWALKKEY  HITPARKEDCAR  
0             0             N  
1             0             N  
2             0             N  
3             0             N  
4             0             N  

[5 rows x 38 columns]

In [2]:
df_accd=df_accd.drop(['X','Y','OBJECTID','ADDRTYPE','JUNCTIONTYPE','SEVERITYCODE.1', 'COLLISIONTYPE', 'SDOT_COLCODE', 'SDOT_COLDESC', 'ST_COLCODE', 'SEGLANEKEY', 'CROSSWALKKEY', 'HITPARKEDCAR','INCKEY','ST_COLDESC','COLDETKEY','REPORTNO','STATUS','INTKEY','LOCATION','EXCEPTRSNCODE','EXCEPTRSNDESC','SEVERITYDESC','PERSONCOUNT','PEDCOUNT','PEDCYLCOUNT','VEHCOUNT','INCDTTM','INATTENTIONIND','PEDROWNOTGRNT','SDOTCOLNUM','SPEEDING'], axis = 1)

In [3]:
import numpy as np
df_accd.replace("", np.nan, inplace = True)
df_accd.replace("Unknown", np.nan, inplace = True)
missing_data = df_accd.isnull()
missing_data.head(5)
for column in missing_data.columns.values.tolist():
    print(column)
    print (missing_data[column].value_counts())
    print("")

SEVERITYCODE
False    194673
Name: SEVERITYCODE, dtype: int64

INCDATE
False    194673
Name: INCDATE, dtype: int64

UNDERINFL
False    189789
True       4884
Name: UNDERINFL, dtype: int64

WEATHER
False    174501
True      20172
Name: WEATHER, dtype: int64

ROADCOND
False    174583
True      20090
Name: ROADCOND, dtype: int64

LIGHTCOND
False    176030
True      18643
Name: LIGHTCOND, dtype: int64



In [4]:
df_accd.dropna(subset=["SEVERITYCODE", "INCDATE", "UNDERINFL", "WEATHER", "ROADCOND", "LIGHTCOND"], axis=0, inplace=True)
# reset index, because we droped two rows
df_accd.reset_index(drop=True, inplace=True)

In [5]:
df_accd['INCDATE'] = pd.to_datetime(df_accd['INCDATE'])
df_accd['Weeday_Name'] = df_accd.INCDATE.dt.weekday_name
df_accd.head()

SEVERITYCODE                   INCDATE UNDERINFL   WEATHER ROADCOND  \
0           Injury 2013-03-27 00:00:00+00:00         N  Overcast      Wet   
1  Property Damage 2006-12-20 00:00:00+00:00         N   Raining      Wet   
2  Property Damage 2004-11-18 00:00:00+00:00         N  Overcast      Dry   
3  Property Damage 2013-03-29 00:00:00+00:00         N     Clear      Dry   
4           Injury 2004-01-28 00:00:00+00:00         N   Raining      Wet   

                 LIGHTCOND Weeday_Name  
0                 Daylight   Wednesday  
1  Dark - Street Lights On   Wednesday  
2                 Daylight    Thursday  
3                 Daylight      Friday  
4                 Daylight   Wednesday

In [6]:
df_accd = df_accd.iloc[:-100000]

In [8]:
import pandas as pd

from matplotlib import pyplot as plt
import seaborn as sns

df_weather = df_accd.pivot_table(values='ROADCOND',index='WEATHER', columns='SEVERITYCODE', aggfunc='count')

ax = df_weather.plot(kind='bar', figsize=(200, 80), rot=90,color = ['#5cb85c','#5bc0de'], width=.8, fontsize=200)

ax.set_title('Count of Property Damage & Injury wrt Weather',fontsize=200)

ax.set_facecolor('white')

ax.legend(fontsize=200,facecolor = 'white') 

ax.get_yaxis().set_visible(False)

for p in ax.patches:
    ax.annotate(np.round(p.get_height(),decimals=2), 
                (p.get_x()+p.get_width()/2., p.get_height()), ha='center', va='center', xytext=(0, 10), textcoords='offset points',fontsize = 200)
plt.show()

In [9]:
df_underinfl = df_accd.pivot_table(values='ROADCOND',index='UNDERINFL', columns='SEVERITYCODE', aggfunc='count')

ax = df_underinfl.plot(kind='bar', figsize=(200, 80), rot=90,color = ['#5cb85c','#5bc0de'], width=.8, fontsize=200)

ax.set_title('Count of Property Damage & Injury wrt Under Influence',fontsize=200)

ax.set_facecolor('white')

ax.legend(fontsize=200,facecolor = 'white') 

ax.get_yaxis().set_visible(False)

for p in ax.patches:
    ax.annotate(np.round(p.get_height(),decimals=2), 
                (p.get_x()+p.get_width()/2., p.get_height()), ha='center', va='center', xytext=(0, 10), textcoords='offset points',fontsize = 200)
plt.show()

In [10]:
df_roadcond = df_accd.pivot_table(values='WEATHER',index='ROADCOND', columns='SEVERITYCODE', aggfunc='count')

ax = df_roadcond.plot(kind='bar', figsize=(200, 80), rot=90,color = ['#5cb85c','#5bc0de'], width=.8, fontsize=200)

ax.set_title('Count of Property Damage & Injury wrt Road Condition',fontsize=200)

ax.set_facecolor('white')

ax.legend(fontsize=200,facecolor = 'white') 

ax.get_yaxis().set_visible(False)

for p in ax.patches:
    ax.annotate(np.round(p.get_height(),decimals=2), 
                (p.get_x()+p.get_width()/2., p.get_height()), ha='center', va='center', xytext=(0, 10), textcoords='offset points',fontsize = 200)
plt.show()

In [11]:
df_lightcond = df_accd.pivot_table(values='WEATHER',index='LIGHTCOND', columns='SEVERITYCODE', aggfunc='count')

ax = df_lightcond.plot(kind='bar', figsize=(200, 80), rot=90,color = ['#5cb85c','#5bc0de'], width=.8, fontsize=200)

ax.set_title('Count of Property Damage & Injury wrt Light Condition',fontsize=200)

ax.set_facecolor('white')

ax.legend(fontsize=200,facecolor = 'white') 

ax.get_yaxis().set_visible(False)

for p in ax.patches:
    ax.annotate(np.round(p.get_height(),decimals=2), 
                (p.get_x()+p.get_width()/2., p.get_height()), ha='center', va='center', xytext=(0, 10), textcoords='offset points',fontsize = 200)
plt.show()

In [12]:
df_weekday = df_accd.pivot_table(values='WEATHER',index='Weeday_Name', columns='SEVERITYCODE', aggfunc='count')

ax = df_weekday.plot(kind='bar', figsize=(200, 80), rot=90,color = ['#5cb85c','#5bc0de'], width=.8, fontsize=200)

ax.set_title('Count of Property Damage & Injury wrt Weekday',fontsize=200)

ax.set_facecolor('white')

ax.legend(fontsize=200,facecolor = 'white') 

ax.get_yaxis().set_visible(False)

for p in ax.patches:
    ax.annotate(np.round(p.get_height(),decimals=2), 
                (p.get_x()+p.get_width()/2., p.get_height()), ha='center', va='center', xytext=(0, 10), textcoords='offset points',fontsize = 200)
plt.show()

In [13]:
df_accd=df_accd.drop(['Weeday_Name'], axis = 1)

In [14]:
df_accd=df_accd.drop(['INCDATE'], axis = 1)
df_accd.head()

SEVERITYCODE UNDERINFL   WEATHER ROADCOND                LIGHTCOND
0           Injury         N  Overcast      Wet                 Daylight
1  Property Damage         N   Raining      Wet  Dark - Street Lights On
2  Property Damage         N  Overcast      Dry                 Daylight
3  Property Damage         N     Clear      Dry                 Daylight
4           Injury         N   Raining      Wet                 Daylight

In [15]:
dummy_variable_1 = pd.get_dummies(df_accd["UNDERINFL"])
dummy_variable_2 = pd.get_dummies(df_accd["WEATHER"])
dummy_variable_3 = pd.get_dummies(df_accd["ROADCOND"])
dummy_variable_4 = pd.get_dummies(df_accd["LIGHTCOND"])
df_accd = pd.concat([df_accd, dummy_variable_1], axis=1)
df_accd = pd.concat([df_accd, dummy_variable_2], axis=1)
df_accd = pd.concat([df_accd, dummy_variable_3], axis=1)
df_accd = pd.concat([df_accd, dummy_variable_4], axis=1)
df_accd.head()

SEVERITYCODE UNDERINFL   WEATHER ROADCOND                LIGHTCOND  N  \
0           Injury         N  Overcast      Wet                 Daylight  1   
1  Property Damage         N   Raining      Wet  Dark - Street Lights On  1   
2  Property Damage         N  Overcast      Dry                 Daylight  1   
3  Property Damage         N     Clear      Dry                 Daylight  1   
4           Injury         N   Raining      Wet                 Daylight  1   

   Y  Blowing Sand/Dirt  Clear  Fog/Smog/Smoke  ...  Standing Water  Wet  \
0  0                  0      0               0  ...               0    1   
1  0                  0      0               0  ...               0    1   
2  0                  0      0               0  ...               0    0   
3  0                  0      1               0  ...               0    0   
4  0                  0      0               0  ...               0    1   

   Dark - No Street Lights  Dark - Street Lights Off  Dark - Street Lights On  \
0                        0                         0                        0   
1                        0                         0                        1   
2                        0                         0                        0   
3                        0                         0                        0   
4                        0                         0                        0   

   Dark - Unknown Lighting  Dawn  Daylight  Dusk  Other  
0                        0     0         1     0      0  
1                        0     0         0     0      0  
2                        0     0         1     0      0  
3                        0     0         1     0      0  
4                        0     0         1     0      0  

[5 rows x 32 columns]

In [16]:
Feature = df_accd[['N', 'Y', 'Blowing Sand/Dirt', 'Clear', 'Fog/Smog/Smoke', 'Other', 'Overcast', 'Raining', 'Severe Crosswind', 'Sleet/Hail/Freezing Rain', 'Snowing', 'Dry', 'Ice', 'Oil', 'Other', 'Sand/Mud/Dirt', 'Snow/Slush', 'Standing Water', 'Wet', 'Dark - No Street Lights', 'Dark - Street Lights Off', 'Dark - Street Lights On', 'Dark - Unknown Lighting', 'Dawn', 'Daylight', 'Dusk', 'Other',]]

In [17]:
X=Feature

y = df_accd['SEVERITYCODE'].values

In [18]:
from sklearn import preprocessing
X= preprocessing.StandardScaler().fit(X).transform(X.astype(float))

from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 4)

/opt/conda/envs/Python36/lib/python3.6/site-packages/sklearn/preprocessing/data.py:645: DataConversionWarning: Data with input dtype uint8 were all converted to float64 by StandardScaler.
  return self.partial_fit(X, y)


In [19]:
print ('Train set:', X_train.shape, y_train.shape)
print ('Test set:', X_test.shape, y_test.shape)

Train set: (56408, 33) (56408,)
Test set: (14102, 33) (14102,)


In [20]:
from sklearn.tree import DecisionTreeClassifier 
from sklearn.metrics import jaccard_similarity_score
from sklearn.metrics import f1_score
depth_range = range(1, 10)
jaccard_similarity_score_ = []
f1_score_ = []

for d in depth_range:
    dt = DecisionTreeClassifier(criterion = 'gini', max_depth = d)
    dt.fit(X_train, y_train)
    dt_yhat = dt.predict(X_test)
    jaccard_similarity_score_.append(jaccard_similarity_score(y_test, dt_yhat))
    f1_score_.append(f1_score(y_test, dt_yhat, average = 'weighted'))

/opt/conda/envs/Python36/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/opt/conda/envs/Python36/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


In [21]:
result = pd.DataFrame([jaccard_similarity_score_, f1_score_], index = ['Jaccard', 'F1'], columns = ['d = 1','d = 2','d = 3','d = 4','d = 5','d = 6','d = 7','d = 8','d = 9'])
result.columns.name = 'Evaluation Metrices'
result

Evaluation Metrices     d = 1     d = 2     d = 3     d = 4     d = 5  \
Jaccard              0.686215  0.686215  0.686427  0.686286  0.686286   
F1                   0.558518  0.558518  0.559144  0.558945  0.559076   

Evaluation Metrices     d = 6     d = 7     d = 8     d = 9  
Jaccard              0.685789  0.686073  0.685435  0.685364  
F1                   0.559226  0.559494  0.559183  0.559148

In [25]:
# Main Model Decision Tree

dt_model = DecisionTreeClassifier(criterion = 'gini', max_depth = 3)
dt_model.fit(X_train, y_train)
dt_model

DecisionTreeClassifier(class_weight=None, criterion='gini', max_depth=3,
            max_features=None, max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, presort=False, random_state=None,
            splitter='best')

In [35]:
dt_yhat = dt_model.predict(X_test)
jss2 = round(jaccard_similarity_score(y_test, dt_yhat), 2)
jss2

0.69

In [23]:
from sklearn.linear_model import LogisticRegression 
from sklearn.metrics import log_loss

import matplotlib.pyplot as plt
%matplotlib inline
solvers = ['lbfgs', 'saga', 'liblinear', 'newton-cg', 'sag']
regularization_val = [0.1, 0.01, 0.001]
index = []
accuracy_score = []
iterations = 0

for index1, c in enumerate(regularization_val):
    for index2, solver in enumerate(solvers):
        index.append(index1 + index2 *5)
        iterations +=1
        lr_model = LogisticRegression(C = c, solver = solver)
        lr_model.fit(X_train, y_train)
        lr_yhat = lr_model.predict(X_test)
        y_prob = lr_model.predict_proba(X_test)
        print('Test {}: Accuracy at C = {} when Solver = {} is : {}'.format(iterations, c, solver, log_loss(y_test, y_prob) ))
        accuracy_score.append(log_loss(y_test, y_prob))
                              
    print('\n')

Test 1: Accuracy at C = 0.1 when Solver = lbfgs is : 0.6186618014664765


/opt/conda/envs/Python36/lib/python3.6/site-packages/sklearn/linear_model/sag.py:334: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)


Test 2: Accuracy at C = 0.1 when Solver = saga is : 0.6186612231218291
Test 3: Accuracy at C = 0.1 when Solver = liblinear is : 0.6186604300150287
Test 4: Accuracy at C = 0.1 when Solver = newton-cg is : 0.6186612281832549


/opt/conda/envs/Python36/lib/python3.6/site-packages/sklearn/linear_model/sag.py:334: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)


Test 5: Accuracy at C = 0.1 when Solver = sag is : 0.6186612290486366


Test 6: Accuracy at C = 0.01 when Solver = lbfgs is : 0.6186560556086597


/opt/conda/envs/Python36/lib/python3.6/site-packages/sklearn/linear_model/sag.py:334: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)


Test 7: Accuracy at C = 0.01 when Solver = saga is : 0.6186559256743217
Test 8: Accuracy at C = 0.01 when Solver = liblinear is : 0.6186524409090125
Test 9: Accuracy at C = 0.01 when Solver = newton-cg is : 0.6186559286843399


/opt/conda/envs/Python36/lib/python3.6/site-packages/sklearn/linear_model/sag.py:334: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)


Test 10: Accuracy at C = 0.01 when Solver = sag is : 0.6186559310930426


Test 11: Accuracy at C = 0.001 when Solver = lbfgs is : 0.6186271822954212
Test 12: Accuracy at C = 0.001 when Solver = saga is : 0.6186271885023323
Test 13: Accuracy at C = 0.001 when Solver = liblinear is : 0.6189534912649313
Test 14: Accuracy at C = 0.001 when Solver = newton-cg is : 0.6186272637837754
Test 15: Accuracy at C = 0.001 when Solver = sag is : 0.6186272608383476




In [26]:
# Main Log Regression Model
from sklearn.linear_model import LogisticRegression 

lr_model = LogisticRegression(C = 0.001, solver = 'liblinear')
lr_model.fit(X_train, y_train)
lr_model

LogisticRegression(C=0.001, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='warn',
          n_jobs=None, penalty='l2', random_state=None, solver='liblinear',
          tol=0.0001, verbose=0, warm_start=False)

In [27]:
from sklearn.svm import SVC 
from sklearn.metrics import jaccard_similarity_score
from sklearn.metrics import f1_score

import matplotlib.pyplot as plt
%matplotlib inline

In [28]:
kernel_func = ['sigmoid', 'poly', 'rbf', 'linear']
accuracy_score = []

for k in kernel_func:
    svc_model = SVC(C = 0.01, gamma = 'auto', kernel = k)
    svc_model.fit(X_train, y_train)
    svc_yhat = svc_model.predict(X_test)
    accuracy_score.append(f1_score(y_test, svc_yhat, average = 'weighted'))

/opt/conda/envs/Python36/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/opt/conda/envs/Python36/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


In [31]:

for i in range(0, len(accuracy_score)):
    print("k = {} has a Score = {} ".format(i+1, accuracy_score[i]))


k = 1 has a Score = 0.5585180081732743 
k = 2 has a Score = 0.5587931865286121 
k = 3 has a Score = 0.5585180081732743 
k = 4 has a Score = 0.5586426974635496 


In [32]:
#Main Model Support Vector Machine
svc_model = SVC(C = 0.01, gamma = 'auto', kernel = 'poly')
svc_model.fit(X_train, y_train)
svc_model

SVC(C=0.01, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma='auto', kernel='poly',
  max_iter=-1, probability=False, random_state=None, shrinking=True,
  tol=0.001, verbose=False)

In [ ]:
from sklearn.neighbors import KNeighborsClassifier as knn
from sklearn.metrics import accuracy_score

ks = range(1, 10)
mean_accuracy = []

for n in ks:
    knn_model  = knn(n_neighbors = n)
    knn_model.fit(X_train, y_train)
    knn_yhat = knn_model.predict(X_test)
    mean_accuracy.append(accuracy_score(y_test, knn_yhat))

In [33]:
print("Hello")

Hello


In [36]:
# Jaccard
from sklearn.metrics import jaccard_similarity_score

# Decision Tree
dt_yhat = dt_model.predict(X_test)
jss1 = round(jaccard_similarity_score(y_test, dt_yhat), 2)

# Support Vector Machine
svc_yhat = svc_model.predict(X_test)
jss2 = round(jaccard_similarity_score(y_test, svc_yhat), 2)

# Logistic Regression
lr_yhat = lr_model.predict(X_test)
jss3 = round(jaccard_similarity_score(y_test, lr_yhat), 2)

jss_list = [jss1, jss2, jss3]
jss_list

[0.69, 0.69, 0.69]

In [37]:
# F1_score
from sklearn.metrics import f1_score

# Decision Tree
dt_yhat = dt_model.predict(X_test)
f1 = round(f1_score(y_test, dt_yhat, average = 'weighted'), 2)

# Support Vector Machine
svc_yhat = svc_model.predict(X_test)
f2 = round(f1_score(y_test, svc_yhat, average = 'weighted'), 2)

# Logistic Regression
lr_yhat = lr_model.predict(X_test)
f3 = round(f1_score(y_test, lr_yhat, average = 'weighted'), 2)

f1_list = [f1, f2, f3]
f1_list

[0.56, 0.56, 0.56]

In [52]:
# log loss
from sklearn.metrics import log_loss

# Logistic Regression
lr_prob = lr_model.predict_proba(X_test)
ll_list = ['NA','NA', round(log_loss(y_test, lr_prob), 2)]
ll_list

['NA', 'NA', 0.62]

In [50]:
columns = ['Decision Tree', 'SVM', 'Logistic Regression']
index = ['Jaccard', 'F1-score', 'Logloss']



In [53]:
accuracy_df = pd.DataFrame([jss_list, f1_list, ll_list], index = index, columns = columns)

In [54]:
accuracy_df1 = accuracy_df.transpose()
accuracy_df1.columns.name = 'Algorithm'
accuracy_df1

Algorithm           Jaccard F1-score Logloss
Decision Tree          0.69     0.56      NA
SVM                    0.69     0.56      NA
Logistic Regression    0.69     0.56    0.62